# Introdução

In [1]:
import os
import re
import time
import json
import folium
import random
import requests
import numpy as np
import pandas as pd
import seaborn as sns
import geopandas as gpd
from folium import plugins
from osgeo import gdal, osr
from bs4 import BeautifulSoup
from tqdm.notebook import trange, tqdm

<br>

# Layer: UGRHIs

In [2]:
# Lê o arquivo csv com o nome dos municípios
df = pd.read_csv(    
    'https://raw.githubusercontent.com/michelmetran/sp/main/data/tabs/tab_municipio_ugrhi.csv',
)

# Lê o arquivo csv com o nome dos municípios
gdf = gpd.read_file(
    'https://raw.githubusercontent.com/michelmetran/sp/main/data/shps/sp_250k_wgs84.geojson',
)
gdf.drop(['municipio_nome'], axis=1, inplace=True)
gdf['id_municipio'] = gdf['id_municipio'].astype(int)
gdf['geometry'] = gdf.simplify(0.0015)

# Merge
gdf = gdf.merge(
    df,
    on='id_municipio',
    how='left'
)

# Save geojson
gdf.to_file(
    os.path.join('data', 'shps', 'sp_ugrhi.geojson'),
    driver='GeoJSON',
    encoding='utf-8'
)

# Results
gdf.head()

id_municipio                                           geometry  \
0       3500105  POLYGON ((-51.05425 -21.40465, -51.04624 -21.4...   
1       3500204  POLYGON ((-49.65795 -21.20333, -49.65361 -21.2...   
2       3500303  POLYGON ((-46.97640 -21.96818, -46.97399 -21.9...   
3       3500402  POLYGON ((-46.73501 -21.81891, -46.72104 -21.8...   
4       3500501  POLYGON ((-46.60614 -22.44173, -46.59592 -22.4...   

     municipio_nome  id_ugrhi       nome_ugrhi  
0        Adamantina        21            Peixe  
1            Adolfo        16  Tietê / Batalha  
2             Aguaí         9       Mogi-Guaçu  
3    Águas da Prata         9       Mogi-Guaçu  
4  Águas de Lindóia         9       Mogi-Guaçu

In [3]:
def layer_ugrhi(input_geojson, m):
    # 
    gdf = gpd.read_file(input_geojson)

    # Column with category
    col_categories = 'nome_ugrhi'

    # Set palette
    palette_polygon = 'Paired'

    # Get list of unique values
    categories = set(gdf[col_categories])
    categories = list(categories)
    categories.sort()

    # See the palette chosed
    pal = sns.color_palette(palette_polygon, n_colors=len(categories))

    # Set dictionary
    color_polygon = dict(zip(categories, pal.as_hex()))
    
    # 
    folium.GeoJson(
        gdf,        
        name='UGRHIs',
        smooth_factor=1.0,
        zoom_on_click=False,
        show=False,
        embed=False,
        style_function=lambda x: {
            'fillColor': color_polygon[x['properties'][col_categories]],
            'color': color_polygon[x['properties'][col_categories]],
            'weight': 1,
            'fillOpacity': 0.2,            
        },
        highlight_function=lambda x: {
            'weight': 3,
            'fillOpacity': 0.6,
        },
        tooltip=folium.features.GeoJsonTooltip(
            fields=['municipio_nome', 'nome_ugrhi'],
            aliases=['Munícipio', 'UGRHI'],
            sticky=True,
            opacity=0.9,
            direction='right',
        ),
    #     popup=folium.GeoJsonPopup(
    #         ['popup'],
    #         parse_html=False,
    #         max_width='400',
    #         show=False,
    #         labels=False,
    #         sticky=True,            
    #     )        
    ).add_to(m)
    return m

<br>

# Layer: RMs

In [4]:
# Lê o arquivo csv com o nome dos municípios
df = pd.read_csv(    
    'https://raw.githubusercontent.com/michelmetran/sp/main/data/tabs/tab_rms.csv',
)

# Lê o arquivo csv com o nome dos municípios
gdf = gpd.read_file(
    'https://raw.githubusercontent.com/michelmetran/sp/main/data/shps/sp_250k_wgs84.geojson',
)
gdf.drop(['municipio_nome'], axis=1, inplace=True)
gdf['id_municipio'] = gdf['id_municipio'].astype(int)
gdf['geometry'] = gdf.simplify(0.0015)

# Merge
gdf = gdf.merge(
    df,
    on='id_municipio',
    how='right'
)

# Save geojson
gdf.to_file(
    os.path.join('data', 'shps', 'sp_rms.geojson'),
    driver='GeoJSON',
    encoding='utf-8'
)

# Results
gdf.head()

id_municipio                                           geometry  \
0       3503000  POLYGON ((-47.79380 -20.06856, -47.78470 -20.0...   
1       3508207  POLYGON ((-47.66749 -20.12405, -47.66690 -20.1...   
2       3513207  POLYGON ((-47.33500 -20.27123, -47.32484 -20.2...   
3       3516200  POLYGON ((-47.30482 -20.41847, -47.29935 -20.4...   
4       3517406  POLYGON ((-48.44859 -20.12878, -48.44199 -20.1...   

      municipio_nome                       nome_rm              legislacao  \
0            Aramina  Aglomeração Urbana de Franca  Lei Complementar 1.323   
1          Buritizal  Aglomeração Urbana de Franca  Lei Complementar 1.323   
2  Cristais Paulista  Aglomeração Urbana de Franca  Lei Complementar 1.323   
3             Franca  Aglomeração Urbana de Franca  Lei Complementar 1.323   
4             Guaíra  Aglomeração Urbana de Franca  Lei Complementar 1.323   

         data                       legislacao_data  
0  2018-05-22  Lei Complementar 1.323 de 22.05.2018  
1  2018-05-22  Lei Complementar 1.323 de 22.05.2018  
2  2018-05-22  Lei Complementar 1.323 de 22.05.2018  
3  2018-05-22  Lei Complementar 1.323 de 22.05.2018  
4  2018-05-22  Lei Complementar 1.323 de 22.05.2018

In [24]:
sns.dark_palette('#808080', reverse=True, as_cmap=False, n_colors=5)

[(0.5019607843137255, 0.5019607843137255, 0.5019607843137255),
 (0.41305174966086156, 0.413053165666333, 0.41304818037951174),
 (0.3241427150079977, 0.3241455470189405, 0.324135576445298),
 (0.2352336803551338, 0.23523792837154806, 0.23522297251108426),
 (0.1477138493687209, 0.1477194912655211, 0.14769962801334263)]

In [25]:
def layer_rms(input_geojson, m):
    # 
    gdf = gpd.read_file(input_geojson)

    # Column with category
    col_categories = 'nome_rm'

    # Set palette
    palette_polygon = 'Paired'

    # Get list of unique values
    categories = set(gdf[col_categories])
    categories = list(categories)
    categories.sort()

    # See the palette chosed
    pal = sns.color_palette(palette_polygon, n_colors=len(categories))
    pal = sns.dark_palette('#808080', reverse=True, as_cmap=False, n_colors=len(categories))

    # Set dictionary
    color_polygon = dict(zip(categories, pal.as_hex()))
    
    # 
    folium.GeoJson(
        gdf,
        name='RMs - AUs',
        smooth_factor=1.0,
        zoom_on_click=False,
        show=False,
        embed=False,
        style_function=lambda x: {
            'fillColor': color_polygon[x['properties'][col_categories]],
            'color': color_polygon[x['properties'][col_categories]],
            'weight': 1,
            'fillOpacity': 0.2,
            'fillPattern': plugins.pattern.StripePattern(angle=-45),
        },
        highlight_function=lambda x: {
            'weight': 3,
            'fillOpacity': 0.6,
        },
        tooltip=folium.features.GeoJsonTooltip(
            fields=['municipio_nome', 'nome_rm'],
            aliases=['Munícipio', 'RM - AU'],
            sticky=True,
            opacity=0.9,
            direction='right',
        ),
    #     popup=folium.GeoJsonPopup(
    #         ['popup'],
    #         parse_html=False,
    #         max_width='400',
    #         show=False,
    #         labels=False,
    #         sticky=True,            
    #     )        
    ).add_to(m)
    return m

<br>

# Layer: URAEs

In [26]:
# Lê o arquivo csv com o nome dos municípios
df = pd.read_csv(
    'https://raw.githubusercontent.com/michelmetran/pl251/main/data/tabs/tab_municipio_pl251.csv',
    #os.path.join('data', 'tabs', 'tab_municipio_pl251.csv'),
)

# Lê o arquivo csv com o nome dos municípios
gdf = gpd.read_file(
    'https://raw.githubusercontent.com/michelmetran/sp/main/data/shps/sp_250k_wgs84.geojson',
)
gdf.drop(['municipio_nome'], axis=1, inplace=True)
gdf['id_municipio'] = gdf['id_municipio'].astype(int)
gdf['geometry'] = gdf.simplify(0.0015)

# Merge
gdf = gdf.merge(
    df,
    on='id_municipio',
    how='left'
)

# Results
gdf.head()

id_municipio                                           geometry  \
0       3500105  POLYGON ((-51.05425 -21.40465, -51.04624 -21.4...   
1       3500204  POLYGON ((-49.65795 -21.20333, -49.65361 -21.2...   
2       3500303  POLYGON ((-46.97640 -21.96818, -46.97399 -21.9...   
3       3500402  POLYGON ((-46.73501 -21.81891, -46.72104 -21.8...   
4       3500501  POLYGON ((-46.60614 -22.44173, -46.59592 -22.4...   

     municipio_nome  id           unidade  
0        Adamantina   1  URAE 1 - Sudeste  
1            Adolfo   2  URAE 1 - Sudeste  
2             Aguaí   3  URAE 1 - Sudeste  
3    Águas da Prata   4  URAE 1 - Sudeste  
4  Águas de Lindóia   1    URAE 4 - Norte

<br>

## Create pop up's column

In [27]:
# Add Field
def popup_html(row):
    html = """
    <div>
    <p><b>{}</b> pertence à:
    <h4><b>{}</b></h4></p>
    </div>
    """.format(
        '' if pd.isnull(row['municipio_nome']) else '{}'.format(row['municipio_nome']),
        '' if pd.isnull(row['unidade'])        else '{}'.format(row['unidade']),
    )
    
    html = html.replace('\n','')
    html = re.sub('\s\s+' , ' ', html) # Remove Espaços no meio
    html = html.strip()
    return html

In [28]:
# Calculate PopUps
gdf['popup'] = gdf.apply(popup_html, axis=1)

<br>

## Adjust Table

In [29]:
# Delete Columns
gdf.drop(['id'], axis=1, inplace=True)
print(gdf.columns)

Index(['id_municipio', 'geometry', 'municipio_nome', 'unidade', 'popup'], dtype='object')


In [30]:
# Save geojson
gdf.to_file(
    os.path.join('data', 'shps', 'sp_urae.geojson'),
    driver='GeoJSON',
    encoding='utf-8'
)

# Results
gdf.head()

id_municipio                                           geometry  \
0       3500105  POLYGON ((-51.05425 -21.40465, -51.04624 -21.4...   
1       3500204  POLYGON ((-49.65795 -21.20333, -49.65361 -21.2...   
2       3500303  POLYGON ((-46.97640 -21.96818, -46.97399 -21.9...   
3       3500402  POLYGON ((-46.73501 -21.81891, -46.72104 -21.8...   
4       3500501  POLYGON ((-46.60614 -22.44173, -46.59592 -22.4...   

     municipio_nome           unidade  \
0        Adamantina  URAE 1 - Sudeste   
1            Adolfo  URAE 1 - Sudeste   
2             Aguaí  URAE 1 - Sudeste   
3    Águas da Prata  URAE 1 - Sudeste   
4  Águas de Lindóia    URAE 4 - Norte   

                                               popup  
0  <div> <p><b>Adamantina</b> pertence à: <h4><b>...  
1  <div> <p><b>Adolfo</b> pertence à: <h4><b>URAE...  
2  <div> <p><b>Aguaí</b> pertence à: <h4><b>URAE ...  
3  <div> <p><b>Águas da Prata</b> pertence à: <h4...  
4  <div> <p><b>Águas de Lindóia</b> pertence à: <...

In [31]:
def layer_urae(input_geojson, m):    
    gdf = gpd.read_file(input_geojson)
    
    # Column with category
    col_categories = 'unidade'
    
    # Set palette
    palette_polygon = 'Paired'

    # Get list of unique values
    categories = set(gdf[col_categories])
    categories = list(categories)
    categories.sort()

    # See the palette chosed
    pal = sns.color_palette(palette_polygon, n_colors=len(categories))
    
    # Set dictionary
    color_polygon = dict(zip(categories, pal.as_hex()))
    color_polygon['URAE 1 - Sudeste'] = '#0505B4'
    color_polygon['URAE 2 - Centro'] = '#FF2E2F'
    color_polygon['URAE 3 - Leste'] = '#FEFF01'
    color_polygon['URAE 4 - Norte'] = '#31B505'    
    
    # dddd
    folium.GeoJson(
        gdf,
        name='URAEs',
        smooth_factor=1.0,
        zoom_on_click=False,
        embed=False,
        show=True,
        style_function=lambda x: {
            'fillColor': color_polygon[x['properties'][col_categories]],
            'color': color_polygon[x['properties'][col_categories]],
            'weight': 1,
            'fillOpacity': 0.3,
        },
        highlight_function=lambda x: {
            'weight': 3,
            'fillOpacity': 0.6,
        },
        tooltip=folium.features.GeoJsonTooltip(
            fields=['municipio_nome', 'unidade'],
            aliases=['Munícipio', 'Unidade'],
            sticky=True,
            opacity=0.9,
            direction='right',
        ),
        popup=folium.GeoJsonPopup(
            ['popup'],
            parse_html=False,
            max_width='400',
            show=False,
            labels=False,
            sticky=True,            
        )        
    ).add_to(m)    
    return m

<br>

## Get Centroid

In [32]:
def get_centroid(gdf):
    gdf['apenasparacentroid'] = 35
    gdf_dissolve = gdf.dissolve(by='apenasparacentroid')
    gdf_centroid = gdf_dissolve.representative_point()
    gdf = gdf.drop('apenasparacentroid', axis=1)
    return [float(gdf_centroid.y), float(gdf_centroid.x)]

In [33]:
list_centroid = get_centroid(gdf)
list_centroid

[-22.545968889465207, -49.56185387118866]

# Folium Map

In [34]:
def map_bomb(bbox):
    # Create Map
    m = folium.Map(
        location=[-22.545968889465207, -49.56185387118866],
        zoom_start=6,
        min_zoom=6,
        max_zoom=11,
        max_bounds=True,
        min_lon = bbox['min_lon']*(101/100),
        max_lon = bbox['max_lon']*(99/100),        
        min_lat = bbox['min_lat']*(101/100),
        max_lat = bbox['max_lat']*(99/100),
        #zoom_delta=0.1,
        tiles=None
    )
    
    # Add Base Map
    folium.TileLayer(
        'cartodbpositron',
        name='BaseMap',
        control=False,
    ).add_to(m)

    # Add Layers
    layer_urae(os.path.join('data', 'shps', 'sp_urae.geojson'), m)
    layer_rms(os.path.join('data', 'shps', 'sp_rms.geojson'), m)
    layer_ugrhi(os.path.join('data', 'shps', 'sp_ugrhi.geojson'), m)

    # Plugins
    m.fit_bounds(m.get_bounds())
    plugins.Fullscreen(
        position='topleft',
        title='Clique para Maximizar',
        title_cancel='Mininizar',
    ).add_to(m)
    folium.LayerControl('topright', collapsed=False).add_to(m)
    return m

In [35]:
# Map without Bounds
bbox = {
    'max_lat': 0,
    'max_lon': 0,
    'min_lat': 0,
    'min_lon': 0,
}
m = map_bomb(bbox)

# Map with Bounds
bbox = {
    'max_lat': m.get_bounds()[1][0],
    'min_lat': m.get_bounds()[0][0],
    'max_lon': m.get_bounds()[1][1],
    'min_lon': m.get_bounds()[0][1],
}
m = map_bomb(bbox)

# Results
print(bbox)
m.save(os.path.join('maps', 'pl251_map.html'))
m

{'max_lat': -19.779655795, 'min_lat': -25.357940277, 'max_lon': -44.161365164, 'min_lon': -53.10904723}
